In [31]:
import requests, pandas as pd, numpy as np

API = "https://data.boston.gov/api/3/action/datastore_search_sql"

DATASETS = {
    "building_permits": "6ddcd912-32a0-43df-9908-63574f8c7e77",
    "moving_truck_permits": "fde6709d-62a7-4523-a8eb-76eac2004f4b",
    "code_enforcement_violations": "90ed3816-5e70-443c-803d-9a71f44470be",
}


def find_latlon_cols(res_id):
    q = f'SELECT * FROM "{res_id}" LIMIT 1'
    cols = pd.DataFrame(requests.get(API, params={"sql": q}).json()["result"]["records"]).columns
    L = [c for c in cols if "lat" in c.lower()]
    G = [c for c in cols if "lon" in c.lower() or "long" in c.lower()]
    lat = next((c for c in cols if c.lower() in {"y_latitude","latitude"}), (L[0] if L else None))
    lon = next((c for c in cols if c.lower() in {"x_longitude","longitude"}), (G[0] if G else None))
    return lat, lon

def pick_order_col(res_id):
    # Try to find a timestamp-like column; else fall back to CKAN's auto _id
    cand_order = [
        "issued_date", "issue_date", "open_dt", "create_date", "created_date",
        "updated_dt", "updated_at", "violation_date", "case_status_date",
        "date", "Date", "timestamp", "Timestamp", "_id", "STATUS_DTTM", "ISSUED_DATE"
    ]
    q = f'SELECT * FROM "{res_id}" LIMIT 1'
    cols = pd.DataFrame(requests.get(API, params={"sql": q}).json()["result"]["records"]).columns
    for c in cand_order:
        if c in cols: 
            return c
    return "_id"

def fetch_coords_latest(res_id, lat_col, lon_col, n=5000, order_col=None, descending=True):
    order_col = order_col or pick_order_col(res_id)
    direction = "DESC" if descending else "ASC"
    q = (
        f'SELECT "{lat_col}" AS lat, "{lon_col}" AS lon '
        f'FROM "{res_id}" '
        f'WHERE "{lat_col}" IS NOT NULL AND "{lon_col}" IS NOT NULL '
        f'ORDER BY "{order_col}" {direction} '
        f'LIMIT {int(n)}'
    )
    r = requests.get(API, params={"sql": q}).json()["result"]["records"]
    if not r:
        return np.empty((0,2))
    df = pd.DataFrame(r).replace("", np.nan).dropna(subset=["lat","lon"])
    return df.astype(float)[["lat","lon"]].to_numpy()


# Fetch coordinates for all datasets
coords = {}
for name, rid in DATASETS.items():
    latc, lonc = find_latlon_cols(rid)
    xy = fetch_coords_latest(rid, latc, lonc)
    coords[name] = xy
    print(f"{name}: {len(xy)} points, cols=({latc}, {lonc})")


building_permits: 5000 points, cols=(y_latitude, x_longitude)
moving_truck_permits: 5000 points, cols=(lat, long)
code_enforcement_violations: 5000 points, cols=(latitude, longitude)


In [32]:
# Boston approx extent (min_lon, min_lat, max_lon, max_lat)
BOS_BBOX = (-71.1912, 42.2279, -70.9220, 42.3973)

def clean_xy(xy, bbox=BOS_BBOX):
    if xy.size == 0:
        return xy
    min_lon, min_lat, max_lon, max_lat = bbox
    lat, lon = xy[:,0], xy[:,1]
    mask = (lat >= min_lat) & (lat <= max_lat) & (lon >= min_lon) & (lon <= max_lon)
    return xy[mask]

# Apply cleaning per dataset
for name in list(coords.keys()):
    before = len(coords[name])
    coords[name] = clean_xy(coords[name], BOS_BBOX)
    after = len(coords[name])
    print(f"{name}: kept {after}/{before} inside Boston bbox")


building_permits: kept 5000/5000 inside Boston bbox
moving_truck_permits: kept 5000/5000 inside Boston bbox
code_enforcement_violations: kept 4999/5000 inside Boston bbox


In [33]:
from scipy.stats import gaussian_kde
from sklearn.preprocessing import StandardScaler
import folium, matplotlib.cm as cm, matplotlib.colors as colors





def make_grid(all_xy, n, pad=1e-3):
    mn = all_xy.min(0) - pad
    mx = all_xy.max(0) + pad
    lat = np.linspace(mn[0], mx[0], n+1)
    lon = np.linspace(mn[1], mx[1], n+1)
    latc = (lat[:-1] + lat[1:]) / 2
    lonc = (lon[:-1] + lon[1:]) / 2
    LON, LAT = np.meshgrid(lonc, latc)
    grid = np.column_stack([LAT.ravel(), LON.ravel()])
    return grid, n, (lat, lon)

def kde_on_grid(xy, grid):
    if xy.size == 0:
        return np.zeros(len(grid))
    xy = xy[np.isfinite(xy).all(1)]
    if len(xy) == 0:
        return np.zeros(len(grid))
    kde = gaussian_kde(xy.T, bw_method="scott")
    return kde(grid.T)

# Build grid over combined extent
all_xy = np.vstack([v for v in coords.values() if v.size])
grid, N, _ = make_grid(all_xy, n=40)

# Smoothed distribution (KDE) per dataset
features = {}
for name, xy in coords.items():
    features[name] = kde_on_grid(xy, grid)

# Assemble feature table
out = pd.DataFrame({
    "row": np.repeat(np.arange(N), N),
    "col": np.tile(np.arange(N), N),
    "lat": grid[:,0],
    "lon": grid[:,1],
    **features
})

# Normalize only feature columns
feat_cols = list(features.keys())
scaler = StandardScaler()
out[feat_cols] = scaler.fit_transform(out[feat_cols])

print(out.head())  # Ready for clustering


   row  col        lat        lon  building_permits  moving_truck_permits  \
0    0    0  42.236683 -71.173062         -0.773508             -0.435489   
1    0    1  42.236683 -71.168574         -0.770276             -0.435489   
2    0    2  42.236683 -71.164086         -0.762900             -0.435489   
3    0    3  42.236683 -71.159598         -0.744822             -0.435488   
4    0    4  42.236683 -71.155110         -0.707605             -0.435488   

   code_enforcement_violations  
0                    -0.651606  
1                    -0.651346  
2                    -0.650743  
3                    -0.648606  
4                    -0.641783  


In [34]:
# fit clusterers (keep as-is)
X = out[feat_cols].to_numpy(dtype=float)
k = 5
out["km"]  = KMeans(n_clusters=k, n_init=10, random_state=0).fit_predict(X)
out["db"]  = DBSCAN(eps=0.5, min_samples=5).fit_predict(X)
out["hac"] = AgglomerativeClustering(n_clusters=k).fit_predict(X)

# grid cell size from lat/lon extent and N
cell_dlat = (out["lat"].max() - out["lat"].min()) / N
cell_dlon = (out["lon"].max() - out["lon"].min()) / N

def layer_for(df, label_col, name):
    fg = folium.FeatureGroup(name=name, show=True)
    labs = df[label_col].to_numpy()
    uniq = sorted(set(labs))
    cmap = cm.get_cmap("tab20", max(len(uniq), 1))
    # map labels -> colors; DBSCAN noise (-1) gray
    lut = {lab: colors.to_hex(cmap(i/ max(len(uniq)-1, 1))) for i, lab in enumerate(uniq) if lab != -1}
    for _, r in df.iterrows():
        lab = r[label_col]
        color = "#9e9e9e" if lab == -1 else lut[lab]
        lat, lon = float(r["lat"]), float(r["lon"])
        bounds = [
            [lat - cell_dlat/2, lon - cell_dlon/2],
            [lat - cell_dlat/2, lon + cell_dlon/2],
            [lat + cell_dlat/2, lon + cell_dlon/2],
            [lat + cell_dlat/2, lon - cell_dlon/2],
        ]
        folium.Polygon(bounds, color=color, weight=0.5, fill=True, fill_opacity=0.55).add_to(fg)
    return fg

# base map
m = folium.Map(location=[out["lat"].mean(), out["lon"].mean()], zoom_start=12, tiles="cartodbpositron")
m.add_child(layer_for(out, "km",  "K-Means"))
m.add_child(layer_for(out, "db",  "DBSCAN (-1=noise)"))
m.add_child(layer_for(out, "hac", "Hierarchical"))
folium.LayerControl(collapsed=False).add_to(m)

# In Jupyter: just put `m` on the last line to display; or save:
# m.save("boston_clusters.html")
m
